<a href="https://colab.research.google.com/github/srcnor/minding_constraints/blob/master/_notebooks/2021-01-30-herd-immunity-ii.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Herd Immunity II
> Let's See How Far We've Come

In [1]:
#@title
#hide
import pandas as pd
import numpy as np
import altair as alt
import datetime as dt

In [2]:
#@title
#hide
day = dt.date.today()
day_str = day.strftime("%Y-%m-%d")

inf_df = None
while inf_df is None: #need to fix this to prevent infinite loops
    try:
        url = "https://raw.githubusercontent.com/youyanggu/covid19_projections/master/infection_estimates/past_estimates/" + day_str + "_all_estimates_states.csv" 
        inf_df = pd.read_csv(url)
    except: #need to except only 404 errors
      day = day - dt.timedelta(days=1)
      day_str = day.strftime("%Y-%m-%d")

In [3]:
#@title
#hide
day = dt.date.today() 
day_str = day.strftime("%Y-%m-%d")

inf_df = None
#loop back across date's to pull Gu's latest csv
for x in range(0, 10):  # try up to 10 times
    try:
        url = "https://raw.githubusercontent.com/youyanggu/covid19_projections/master/infection_estimates/past_estimates/" + day_str + "_all_estimates_states.csv" 
        inf_df = pd.read_csv(url)
    except:
      day = day - dt.timedelta(days=1)
      day_str = day.strftime("%Y-%m-%d")
    else:
        break


In [4]:
#@title
#hide_input
vacc_df = pd.read_csv("https://raw.githubusercontent.com/owid/covid-19-data/master/public/data/vaccinations/us_state_vaccinations.csv")

In [5]:
#@title
#hide_input
us_state_abbrev = {
    'Alabama': 'AL',
    'Alaska': 'AK',
    'American Samoa': 'AS',
    'Arizona': 'AZ',
    'Arkansas': 'AR',
    'California': 'CA',
    'Colorado': 'CO',
    'Connecticut': 'CT',
    'Delaware': 'DE',
    'District of Columbia': 'DC',
    'Florida': 'FL',
    'Georgia': 'GA',
    'Guam': 'GU',
    'Hawaii': 'HI',
    'Idaho': 'ID',
    'Illinois': 'IL',
    'Indiana': 'IN',
    'Iowa': 'IA',
    'Kansas': 'KS',
    'Kentucky': 'KY',
    'Louisiana': 'LA',
    'Maine': 'ME',
    'Maryland': 'MD',
    'Massachusetts': 'MA',
    'Michigan': 'MI',
    'Minnesota': 'MN',
    'Mississippi': 'MS',
    'Missouri': 'MO',
    'Montana': 'MT',
    'Nebraska': 'NE',
    'Nevada': 'NV',
    'New Hampshire': 'NH',
    'New Jersey': 'NJ',
    'New Mexico': 'NM',
    'New York': 'NY',
    'North Carolina': 'NC',
    'North Dakota': 'ND',
    'Northern Mariana Islands':'MP',
    'Ohio': 'OH',
    'Oklahoma': 'OK',
    'Oregon': 'OR',
    'Pennsylvania': 'PA',
    'Puerto Rico': 'PR',
    'Rhode Island': 'RI',
    'South Carolina': 'SC',
    'South Dakota': 'SD',
    'Tennessee': 'TN',
    'Texas': 'TX',
    'Utah': 'UT',
    'Vermont': 'VT',
    'Virgin Islands': 'VI',
    'Virginia': 'VA',
    'Washington': 'WA',
    'West Virginia': 'WV',
    'Wisconsin': 'WI',
    'Wyoming': 'WY',
    'United States': 'US', 
}

In [6]:
#@title
#hide_input
vacc_df["location"] = vacc_df.location.replace("New York State", "New York")
vacc_df['state'] =  vacc_df['location'].map(us_state_abbrev)

In [7]:
#@title
#hide_input
df = inf_df.merge(vacc_df, how="left", on = ["date", "state"])

df["date"] = pd.to_datetime(df["date"], format="%Y-%m-%d")
df["pct_vaccinated"] = df["people_vaccinated_per_hundred"]/100
df["pct_fully_vaccinated"] = df["people_fully_vaccinated_per_hundred"]/100

In [8]:
#@title
#hide_input
# Gu's infection estimates lag data by 14 days 
# Going to estimate current infections by using his projections to identify the ratio of identified cases
state_pct_id = inf_df[~inf_df['current_infected_mean'].isna()] # get data where Gu estimates are not null 
state_pct_id = state_pct_id[state_pct_id.groupby("state")['date'].transform(max) == state_pct_id['date']] # get latest date data
state_pct_id["pct_new_identified"] = state_pct_id["daily_positive_7day_ma"]/state_pct_id["new_infected_mean"] # ratio of positive tests to new cases
state_pct_id["population"] = state_pct_id["total_infected_mean"]/state_pct_id["perc_total_infected_mean"]
state_pct_id["latest_total_infected"] = state_pct_id["total_infected_mean"]
state_pct_id = state_pct_id[["state", "pct_new_identified", "population", "latest_total_infected"]]

df = df.merge(state_pct_id, how = "left", on="state")

In [9]:
#@title
#hide_input
df["new_infected_estimate"] = np.where(df["new_infected_mean"].isna(), 
                                       df["daily_positive_7day_ma"]/df["pct_new_identified"], 
                                       df["new_infected_mean"])

df["new_infected_est_cummulative"] = df.groupby(['state', 'date']).sum() \
                                      .groupby(level=0).cumsum().reset_index()["new_infected_estimate"]

df["total_infected_estimate"] = np.where(df["total_infected_mean"].isna(), 
                                         df["new_infected_est_cummulative"],
                                         df["total_infected_mean"])

df["pct_total_infected_estimate"] = df["total_infected_estimate"]/df["population"]

# Vaccine data begins on Jan 13 and is spotty, going to interpolate to fill in gaps
df["pct_vaccinated"] = np.where(df["date"] == pd.to_datetime("2020-12-14"), 
                                1000/df["population"], # assuming all states began vaccination with 1000 people on 12/14
                                df["pct_vaccinated"])
# for interporation, assuming vaccinations grow exponetially 
# log transform -> linear interporolation -> transform back 
df["pct_vaccinated"] = df.groupby('state')["pct_vaccinated"].apply(lambda group: np.exp(np.log(group).interpolate(method="linear")))

In [10]:
#@title
#hide_input
melt_df = df[["date", "state", "population", "pct_total_infected_estimate", "pct_vaccinated"]]. \
            melt(id_vars=['date', 'state', "population"], var_name='immunity_source', value_name='pct_of_pop')

In [11]:
#@title
#hide_input
lab_dict = {"pct_total_infected_estimate":"Infected", "pct_vaccinated":"Vaccinated"}

melt_df["immunity_source"] = melt_df['immunity_source'].map(lab_dict)

In [12]:
#@title
#hide_input
#Make a US row of data 
us_pop = state_pct_id.population.sum()

# us_df = 
melt_df["est_people"] = melt_df["population"] * melt_df["pct_of_pop"]

us_df = melt_df.groupby(["date", "immunity_source"]).sum().reset_index()
us_df["population"] = us_pop
us_df["pct_of_pop"] = us_df["est_people"]/us_df["population"]
us_df["state"] = "US"

melt_df = melt_df.append(us_df)

In [13]:
#@title
#hide_input
state_array = melt_df.state.unique()
melt_df["herd_immunity_estimate"] = .7 

Previously: [Tracking Progress Towards Herd Immunity](http://mindingconstraints.com/2021/01/24/state-immunity-i.html)

I've updated my herd immunity tracker, the key changes are:
* I've added a line at 70%, which seems to be the closest thing to a consensus estimate for the COVID-19 herd immunity threshold, though estimates range from [50 to 90%](https://www.jhsph.edu/covid-19/articles/achieving-herd-immunity-with-covid19.html). We should also expect to see different thresholds in different states due to the ["momentum"](https://twitter.com/CT_Bergstrom/status/1252002993253183488) of the pandemic. A state that is getting more of its immunity from vaccinations and maintaining a low level of ambient infections should see immunity begin to kick in faster than a state where the pandemic is raging. The graph will also no longer rescale on state selection, making comparison easier. 
* I've changed the interpolation of vaccine data from a linear model to a more plausible simple exponential model which honestly just looks better on the graphs. A reminder that interpolation only occurs for the early dates before the CDC began releasing state by state vaccination data, so the most recent data is not modeled. 
* The chart *should* 🤞 now update daily, and will run a day or two behind the current date, aligning with the CDC's publishing schedule. 
* I've also included a table below the graph with my current estimates by state to make cross state comparisons and seeing the latest data easier. 


In [14]:
#@title
#hide_input
alt.data_transformers.disable_max_rows()

dropdown = alt.binding_select(options=state_array)
select = alt.selection_single(name = "Select", fields=['state'], bind=dropdown, init={'state': "US"})

chart = alt.Chart(melt_df, title="Path to Immunity").mark_area().encode(
    x=alt.X(
        "date",
        title=""
    ),
    y=alt.Y(
        "pct_of_pop",
        title="% Population Immune (Estimated)",
        axis=alt.Axis(format=".0%"),
        scale=alt.Scale(domain=(0, 1)),
    ),
    color=alt.Color(
        "immunity_source",
        legend=alt.Legend(title="Immunity Source"),
    ),
    tooltip=['date', alt.Tooltip('date'), 'pct_of_pop', 'immunity_source', 'est_people'],
).add_selection(
    select
).transform_filter(
    select
)#.properties(
    # width=,#"container"
    # height=,#"container"
# )

line = alt.Chart(pd.DataFrame({'y': [.7]})).mark_rule(strokeDash=[10, 10]).encode(y='y')

(chart + line
 ).configure_title(anchor = "start", fontSize = 24
 )

alt.LayerChart(...)

In [15]:
#@title
#hide_input
display_df = df[df["date"] == max(df["date"])] \
  [["date", "state", "population", "total_infected_estimate", "pct_total_infected_estimate", "people_vaccinated", "pct_vaccinated"]]

display_df["people_immune"] = display_df["total_infected_estimate"] + display_df["people_vaccinated"]
display_df["pct_immune"] = display_df["people_immune"] / display_df["population"]


In [16]:
#@title
#hide_input
display_us = display_df.groupby("date").sum().reset_index()
display_us["state"] = "US"
display_us["pct_total_infected_estimate"] = display_us["total_infected_estimate"] / display_us["population"]
display_us["pct_vaccinated"] = display_us["people_vaccinated"] / display_us["population"]
display_us["pct_immune"] = display_us["people_immune"] / display_us["population"]


In [17]:
#@title
#hide_input
display_df = display_us.append(display_df.sort_values("state"))

In [18]:
#@title
#hide_input
us_state_names = {v: k for k, v in us_state_abbrev.items()} #invert dictionary 

display_df['State'] = display_df['state'].map(us_state_names)

In [19]:
#@title
#hide_input
ds = str(max(df["date"]))[0:10]

display_df_final = display_df.rename(columns={"pct_total_infected_estimate": "Estimated % Infected", 
                                             "pct_vaccinated": "% Vaccinated", 
                                             "pct_immune": "Estimated % Immune"})

display_df_final = display_df_final[["State", "Estimated % Infected", "% Vaccinated", "Estimated % Immune"]]

col_df = display_df_final.style \
  .format({"Estimated % Infected":"{:.1%}",
           "% Vaccinated":"{:.1%}",
           "Estimated % Immune":"{:.1%}"}) \
  .background_gradient(cmap = "Blues", subset = ["Estimated % Infected"]) \
  .background_gradient(cmap = "Oranges", subset = ["% Vaccinated"]) \
  .background_gradient(cmap = "Greens", low = 0, high = .7, subset = ["Estimated % Immune"]) \
  .set_caption("Data as of " + ds) \
  .hide_index()

col_df
